In [ ]:
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter
import random
writer = FFMpegWriter(fps=5)
fig = plt.figure(dpi = 100)

maxX = 50
maxY = 50

terrain_prob = [0.001,0.005,0.6,0.3,0.3,0.05]
sticky_prob = [0.001,0.8,0.85,0.8,0.8,0.8]
flam_prob = [0, 0, 0, 0.1, 0.3, 0.6]
flam_out_prob = 0.05


# 0 = burning area = red
# 1 = water = blue 
# 2 = dirt, previously burned area = brown
# 3 = tree = dark green
# 4 = healthy grass = light green
# 5 = dry grass = yellow


color_map = [[173,33,0], [70,97,233], [122,97,66], [18,132,18], [103,196,52], [188,200,50]]



def plot_terrain(terrain):
    plot_matrix = [[-1 for _ in range(maxY)] for _ in range(maxY)]
    for i in range(maxX):
        for j in range(maxY):
            plot_matrix[i][j] = color_map[terrain[i][j]]
    plt.imshow(plot_matrix)
    

def prescribed_burn(terrain):
    p_burned_matrix = [[-1 for _ in range(maxY)] for _ in range(maxY)]
    for i in range(maxX):
        for j in range(maxY):
            if 20 <= i < 22 and 0 <= j < 50:
                p_burned_matrix[i][j] = 2
            else:
                p_burned_matrix[i][j] = terrain[i][j]
                
    return p_burned_matrix

def get_new_terrain(exclusions):
    # here, 'exclusions' is the list of indices that should be excluded from terrain_prob
    new_terrain_prob = []
    for i in range(6):
        if i in exclusions:
            new_terrain_prob.append(0)
        else:
            new_terrain_prob.append(terrain_prob[i])
    new_terrain_prob = [new_terrain_prob[i] / sum(new_terrain_prob) for i in range(6)]
    rand = random.random()
    for i in range(6):
        if rand <= sum(new_terrain_prob[:i+1]):
            return i
    raise ValueError("Random = " + str(rand) + "\nList = " + str(new_terrain_prob))
    
def choose_terrain(ter,i,j):
    exclusions = []
    if i > 0 and j > 0:
        # Flip a coin and give sticky preference to the winner
        rand = random.random()
        exclusions = [ter[i-1][j], ter[i][j-1]]
        if rand <= 0.5:
            prev_ter = ter[i-1][j]
        else:
            prev_ter = ter[i][j-1]
        ter_sticky = sticky_prob[prev_ter]
        if random.random() < ter_sticky:
            return prev_ter
    if len(exclusions) == 0:
        if i > 0:
            left_ter = ter[i-1][j]
            ter_sticky = sticky_prob[left_ter]
            exclusions.append(left_ter)
            if random.random() <= ter_sticky:
                return left_ter
        if j > 0 :
            up_ter = ter[i][j-1]
            ter_sticky = sticky_prob[up_ter]
            exclusions.append(up_ter)
            if random.random() <= ter_sticky:
                return up_ter
    return get_new_terrain(exclusions)


def initialize_fire(terrain):
    new_terrain = list(terrain)
    assert len(new_terrain) == maxX
    assert len(new_terrain[0]) == maxY
    i_fire = random.choice(range(maxX))
    j_fire = random.choice(range(maxY))
    new_terrain[i_fire][j_fire] = 0
    return new_terrain

def has_fire(terrain):
    for i in range(maxX):
        for j in range(maxY):
            if terrain[i][j] == 0:
                return True
    return False
    

def _has_fiery_neighbor(terrain, i, j):
    if i >= 1:
        if terrain[i-1][j] == 0:
            return True
    if i < maxX - 1:
        if terrain[i+1][j] == 0:
            return True
    if j >= 1:
        if terrain[i][j-1] == 0:
            return True
    if j < maxY - 1:
        if terrain[i][j+1] == 0:
            return True
    return False
    
def iterate_fire(terrain):
    new_terrain = [[-1 for _ in range(maxY)] for _ in range(maxY)]
    for i in range(maxY):
        for j in range(maxY):
            new_terrain[i][j] = 0
            
    for i in range(maxX):
        for j in range(maxY):
            # If on fire, see if it goes out.
            if terrain[i][j] == 0:
                if random.random() < flam_out_prob:
                    new_terrain[i][j] = 2
                else:
                    new_terrain[i][j] = 0

            else:
                # This spot is not on fire.
                # See if it catches on fire. It's the job of the 
                # flam_prob list to define what can or can't catch on fire.
                if _has_fiery_neighbor(terrain, i, j):
                    odds_of_catching = flam_prob[terrain[i][j]]
                    if random.random() < odds_of_catching:
                        new_terrain[i][j] = 0  # Burn baby burn!
                    else:
                        new_terrain[i][j] = terrain[i][j]
                else:
                    new_terrain[i][j] = terrain[i][j]

    return new_terrain


terrain = [[-1 for _ in range(maxY)] for _ in range(maxY)]
# terrain = np.ones([maxX,maxY],dtype='uint8')
for i in range(maxX):
    for j in range(maxY):
        terrain[i][j] = choose_terrain(terrain,i,j)

terrain = prescribed_burn(terrain)
terrain = initialize_fire(terrain)



plot_terrain(terrain)

#with writer.saving(fig, "Wildfire.mp4", dpi=100):
#with writer.saving(fig, "Prescribed_Burn_Fire.mp4", dpi=100):
#with writer.saving(fig, "Hot_Dry_Windy.mp4", dpi=100):
with writer.saving(fig, "Hot_Dry_Windy_Prescribed_Burn.mp4", dpi=100):
    # Burn as long as necessary
    while has_fire(terrain):
        terrain = iterate_fire(terrain)
        plot_terrain(terrain)
        # plt.show()
        writer.grab_frame()

    # Final plot
    plot_terrain(terrain)
    writer.grab_frame()


print("Done!")



